In [1]:
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)
import pandas as pd 
from pandas_datareader import data
import requests
import re
import urllib
import io
import matplotlib.pyplot as plt
import altair as alt
from vega_datasets import data
alt.data_transformers.disable_max_rows()


DataTransformerRegistry.enable('default')

In [2]:
fdf=pd.DataFrame
for nodes in ['3']:
    for threads in ['1','2','4','8','16','64','128','256']:
#    for threads in ['1']:
        #url='https://raw.githubusercontent.com/Percona-Lab-results/PXC-8-March2020/master/res-tpcc-GR-'+nodes+'nodes-1writer-BP25G-1/res_thr'+threads+'.txt'
        url='https://raw.githubusercontent.com/Percona-Lab-results/PXC-8-March2020/master/res-tpcc-GR-3nodes-2writer-BP100G-1/res_thr'+threads+'.txt'
        #url='https://raw.githubusercontent.com/Percona-Lab-results/PXC-8-March2020/master/res-tpcc-GR-5nodes-1writer-BP25G-1/res_thr1.txt'
        s=requests.get(url)


        buf=[]
        for line in s.text.splitlines():
            #rint(line)
            if re.match("^[0-9]", line):
                buf.append(line)

        df = pd.DataFrame([x.split(',') for x in buf])
        df['Nodes'] = nodes
        if fdf.empty:
           fdf=df
        else: 
           fdf=fdf.append(df,ignore_index = False)



In [3]:
fdf

0    1       2        3        4        5       6        7     8  \
0        1    1  156.69  4618.78  2126.75  2175.66  316.37    11.65  0.00   
1        2    1  188.06  5180.56  2358.71  2445.74  376.11    11.87  0.00   
2        3    1  192.00  5310.00  2415.00  2511.00  384.00    11.04  1.00   
3        4    1  187.00  5260.04  2390.02  2497.02  373.00    11.65  0.00   
4        5    1  180.00  5161.01  2356.01  2444.01  361.00    11.65  1.00   
...    ...  ...     ...      ...      ...      ...     ...      ...   ...   
1799  1800  256  182.00  4883.03  2207.01  2312.01  364.00    15.27  1.00   
1800  1801  256    1.00    28.00    13.00    14.00    1.00     7.17  0.00   
1801  1802  255  129.00  3867.96  1708.98  1777.98  381.00  3040.14  2.00   
1802  1803  255    0.00     0.00     0.00     0.00    0.00     0.00  0.00   
1803  1804  255    0.00     0.00     0.00     0.00    0.00     0.00  0.00   

         9 Nodes  
0     0.00     3  
1     0.00     3  
2     0.00     3  
3     0.00     3  
4     0.00     3  
...    ...   ...  
1799  0.00     3  
1800  0.00     3  
1801  0.00     3  
1802  0.00     3  
1803  0.00     3  

[14413 rows x 11 columns]

In [4]:
fdf.columns =['sec','threads','tps','read','write','other','v1','rt','v3','v4','nodes']
fdf['tps']=fdf['tps'].astype(float)
fdf['sec']=fdf['sec'].astype(float)
fdf['threads']=fdf['threads'].astype(int)

In [329]:
fdf.query('nodes == "3" and sec>900')

sec  threads      tps      read     write     other       v1      v2  \
900    901.0        1    93.00   2847.01   1300.00   1361.01   186.00   22.69   
901    902.0        1   112.00   2990.99   1357.99   1408.99   224.00   21.11   
902    903.0        1   109.00   3115.00   1429.00   1468.00   218.00   20.00   
903    904.0        1    91.00   2838.00   1317.00   1339.00   182.00   22.28   
904    905.0        1    86.00   2482.01   1141.00   1169.00   172.00   26.20   
...      ...      ...      ...       ...       ...       ...      ...     ...   
1795  1796.0      256  1692.00  49137.97  22361.99  23391.98  3384.00  816.63   
1796  1797.0      256  1541.00  44455.98  20301.99  21071.99  3082.00  861.95   
1797  1798.0      256  1374.00  40558.89  18462.95  19347.95  2747.99  861.95   
1798  1799.0      256  1212.00  33145.10  15047.05  15674.05  2424.01  893.56   
1799  1800.0      256  1715.01  48300.25  22030.12  22840.12  3430.02  909.80   

         v3    v4 nodes  
900    1.00  0.00     3  
901    0.00  0.00     3  
902    0.00  0.00     3  
903    0.00  0.00     3  
904    0.00  0.00     3  
...     ...   ...   ...  
1795  10.00  0.00     3  
1796   7.00  0.00     3  
1797   2.00  0.00     3  
1798   5.00  0.00     3  
1799   9.00  0.00     3  

[7200 rows x 11 columns]

In [11]:


stripplot =  alt.Chart(fdf.query('nodes == "3" and sec<1700'), width=100,title='3nodes, threads 1-256').mark_boxplot(size=8).encode(
    x=alt.X(
        'jitter:Q',
        title=None,
        axis=alt.Axis(values=[0], ticks=True, grid=False, labels=False, title='Threads'),
        scale=alt.Scale(),
    ),
    y=alt.Y('tps:Q',title="Throughput, tps"),
    order='threads:O',
    color=alt.Color('threads:N', legend=None),
    column=alt.Column(
        'threads:N',
        header=alt.Header(
            labelAngle=0,
            titleOrient='top',
            labelOrient='bottom',
            labelAlign='center',
            labelPadding=10,
        ),
    ),
).transform_calculate(
    # Generate Gaussian jitter with a Box-Muller transform
    jitter='sqrt(-2*log(random()))*cos(2*PI*random())'
).configure_facet(
    spacing=0
).configure_view(
    stroke=None
)

stripplot


alt.Chart(...)

In [17]:
stripplot =  alt.Chart(fdf.query('nodes == "3" and sec<1700'), width=800,title='3nodes, threads 1-256').mark_boxplot().encode(
    x=alt.X(
        'threads:N',
        title=None,
        axis=alt.Axis(values=[0], ticks=True, grid=False, labels=False, title='Threads'),
        scale=alt.Scale(),
    ),
    y=alt.Y('tps:Q',title="Throughput, tps"),
    order='threads:N',
    color=alt.Color('threads:N', legend=None),
)

#.configure_facet(
#    spacing=0
#).configure_view(
#    stroke=None
#)

stripplot

alt.Chart(...)

In [8]:
import altair as alt
from vega_datasets import data
alt.data_transformers.disable_max_rows()
from altair.expr import datum

stripplot =  alt.Chart(fdf.query('sec>900 and sec < 1700'), width=100,title='3 nodes, threads 1-256').mark_circle(size=8).encode(
    x=alt.X(
        'jitter:Q',
        title=None,
        axis=alt.Axis(values=[0], ticks=True, grid=False, labels=False),
        scale=alt.Scale(),
    ),
    y=alt.Y('tps:Q', title="Throughput, tps"),
    order='threads:O',
    color='nodes:N',
    facet=alt.Facet('threads:O', columns=5,align="none"),
).transform_calculate(
    # Generate Gaussian jitter with a Box-Muller transform
    jitter='sqrt(-2*log(random()))*cos(2*PI*random())'
).resolve_scale(y='independent').interactive().add_selection(alt.selection_single(empty='all', fields=['nodes']))

#chart = alt.hconcat()
#for threads in ['1','2','4','8','16','64','128','256']:
#    chart |= stripplot.transform_filter(datum.threads == threads)
#chart

stripplot

alt.Chart(...)

In [20]:


alt.Chart(fdf.query('nodes == "3" and sec>900 and sec<1700 and threads=="8"'),width=800,title="8 threads").mark_line().encode(
    x='sec',
    y='tps'
)



alt.Chart(...)

In [30]:
fdf=pd.DataFrame
for nodes in ['3','5']:
#    for threads in ['1','2','4','8','16','64','128','256']:
#    for threads in ['1']:
    #url='https://raw.githubusercontent.com/Percona-Lab-results/PXC-8-March2020/master/res-tpcc-GR-'+nodes+'nodes-1writer-BP25G-1/res_thr'+threads+'.txt'
    url='https://raw.githubusercontent.com/Percona-Lab-results/PXC-8-March2020/master/res-tpcc-GR-'+nodes+'nodes-1writer-BP25G-txrate3100-1/res_thr64.txt'
    #url='https://raw.githubusercontent.com/Percona-Lab-results/PXC-8-March2020/master/res-tpcc-GR-5nodes-1writer-BP25G-1/res_thr1.txt'
    s=requests.get(url)


    buf=[]
    for line in s.text.splitlines():
        #rint(line)
        if re.match("^[0-9]", line):
            buf.append(line)

    df = pd.DataFrame([x.split(',') for x in buf])
    df['Nodes'] = nodes
    if fdf.empty:
       fdf=df
    else: 
       fdf=fdf.append(df,ignore_index = False)

In [36]:
fdf.columns =['sec','threads','tps','read','write','other','v1','rt','v3','v4','nodes']
fdf['tps']=fdf['tps'].astype(float)
fdf['sec']=fdf['sec'].astype(float)
fdf['rt']=fdf['rt'].astype(float)
fdf['threads']=fdf['threads'].astype(int)

In [33]:
fdf

sec  threads      tps      read     write     other       v1      rt  \
0        1.0       64  3023.76  84691.24  38627.06  39872.91  6191.27   23.95   
1        2.0       64  3070.13  87747.71  40053.69  41543.76  6150.26   24.38   
2        3.0       64  3236.00  91827.97  42024.99  43319.99  6483.00   24.83   
3        4.0       64  3140.98  88537.38  40427.72  41828.71  6280.96   26.68   
4        5.0       64  3096.04  87770.03  40091.47  41488.49  6190.07   24.83   
...      ...      ...      ...       ...       ...       ...      ...     ...   
1795  1796.0       64  2999.99  84772.63  38729.83  40013.83  6028.97  179.94   
1796  1797.0       64  3107.95  86374.48  39354.31  40813.28  6206.89   24.83   
1797  1798.0       64  3104.05  90018.56  41106.71  42708.74  6203.11   23.10   
1798  1799.0       64  2992.93  85628.05  39033.11  40611.07  5983.86   24.38   
1799  1800.0       64  3154.62  90155.26  41107.10  42738.91  6309.25   23.95   

         v3    v4 nodes  
0      9.98  0.00     3  
1     13.00  0.00     3  
2     11.00  0.00     3  
3     11.00  0.00     3  
4     21.00  0.00     3  
...     ...   ...   ...  
1795  14.00  0.00     5  
1796  17.00  0.00     5  
1797   7.00  0.00     5  
1798   8.00  0.00     5  
1799  11.00  0.00     5  

[3600 rows x 11 columns]

In [46]:
alt.Chart(fdf,width=800,title="64 threads, 3100 tps incoming rate").mark_point(size=5).encode(
    x='sec',
    y=alt.Y('rt:Q', title="95% response time, ms"),
    color='nodes:N'
)

alt.Chart(...)

In [49]:
alt.Chart(fdf,width=800,title="64 threads, 3100 tps incoming rate").mark_point(size=5).encode(
    x='sec',
    y=alt.Y('tps:Q', title="Throughput, tps"),
    color='nodes:N'
)

alt.Chart(...)